In [5]:
import numpy as np
import trimesh
import slam.io as sio
import nibabel as nib
from scipy.spatial.distance import euclidean
from freesurfer_tools import transform_atlas
import matplotlib
matplotlib.use("Qt5Agg")

In [2]:
annot_paths = [
    "/home/mszul/git/DANC_multilayer_laminar/assets/lh.HCPMMP1.annot",
    "/home/mszul/git/DANC_multilayer_laminar/assets/rh.HCPMMP1.annot"
]
fsavg_sphere_paths = [
    "/home/mszul/git/DANC_multilayer_laminar/assets/lh.sphere.reg.gii",
    "/home/mszul/git/DANC_multilayer_laminar/assets/rh.sphere.reg.gii"
]
fsnat_sphere_paths = [
    "/home/common/bonaiuto/cued_action_meg/derivatives/processed/sub-001/fs/surf/lh.sphere.reg.gii",
    "/home/common/bonaiuto/cued_action_meg/derivatives/processed/sub-001/fs/surf/rh.sphere.reg.gii"
]
pial_path = "/home/common/bonaiuto/cued_action_meg/derivatives/processed/sub-001/fs/surf/pial.gii"
pial_ds_path = "/home/common/bonaiuto/cued_action_meg/derivatives/processed/sub-001/fs/surf/pial.ds.gii"
pial_ds_nodeep = "/home/common/bonaiuto/cued_action_meg/derivatives/processed/sub-001/fs/surf/pial.ds.link_vector.nodeep.gii"
pial_ds_inflated = "/home/common/bonaiuto/cued_action_meg/derivatives/processed/sub-001/fs/surf/pial.ds.inflated.nodeep.gii"
glasser = "/home/mszul/git/DANC_multilayer_laminar/assets/atlas_glasser_2016.csv"

In [3]:
mesh_colors, lab_col_map = transform_atlas(annot_paths, fsavg_sphere_paths, fsnat_sphere_paths, pial_path, pial_ds_path, pial_ds_nodeep)

In [6]:
inflated = sio.load_mesh(pial_ds_inflated)
modified_mesh_colors = [np.append(i[:3], 255) for i in mesh_colors]
inflated.visual.vertex_colors = modified_mesh_colors
inflated.show(viewer="notebook")

In [7]:
target_labels = ['L_V1_ROI']

In [10]:
ROI_maps = {i: [i == j.decode("utf=8") for j in lab_col_map] for i in target_labels}

In [12]:
ROI_maps.keys()

dict_keys(['L_V1_ROI'])

In [67]:
inflated = sio.load_mesh(pial_ds_inflated)

vx_xyz_ROI = np.array(inflated.vertices)[vx_ROI]
dist = np.array([euclidean(vx_xyz_ROI[400], i) for i in vx_xyz_ROI])
cmap = trimesh.visual.interpolate(dist, color_map="hot_r")
cmap[400] = [0,0,0,255]

vtx_col = np.tile([220, 220, 220, 255], [lab_col_map.shape[0], 1])
# cmap = np.tile([200, 200, 200, 255], [vx_xyz_ROI.shape[0], 1])
# cmap[400] = [0,0,0,255]
# cmap[401] = [0,0,0,255]
for k in ROI_maps.keys():
    vtx_col[ROI_maps[k]] = cmap
vtx_col[400] = [0,0,0,255]
inflated.visual.vertex_colors = vtx_col

spheres = []
for i in range(sum(ROI_maps["L_V1_ROI"])):
    vx_ix_peak = np.arange(len(ROI_maps["L_V1_ROI"]))[ROI_maps["L_V1_ROI"]][i]
    peak_loc = np.array(inflated.vertices[vx_ix_peak])
    sphere = trimesh.creation.uv_sphere(radius=0.5)
    sphere.visual.vertex_colors = cmap[i]
    sphere.apply_translation(peak_loc)
    spheres.append(sphere)

scene = trimesh.Scene([inflated])
scene.show(viewer="notebook")